# Replacing Covid Tracking Project Data

- 07/11/21

>NOTE: SEE FINAL WORKFLOW IN "`Replacing Covid Tracking Project - Simplified Workflow.ipynb` and the final script in `data_acquisition.py`

## Goal

- As of 03/07/21 the Covid Tracking Project has stopped collecting new data. 
    - https://covidtracking.com/data
    - This was the primary backbone of my modeling and dashboard and needs to be replaced/ 
    - While I already have an alternative coronavirus source for time series from Kaggle, I want to have the ICU capacity and hospitalization records.
    
    
- Federal Data: 
    - Covid Tracking Project provides info on alternative data sources. https://covidtracking.com/analysis-updates/federal-covid-data-101-how-to-find-data
        - related posts: https://covidtracking.com/analysis-updates/category/federal-covid-data-101
    - They also provide a simple approach for the general public: https://covidtracking.com/analysis-updates/simple-covid-data

- COVID-19 hospitalization data training:
    - Video: https://www.youtube.com/watch?v=TGAHQt1Rkf8
    - Presentaation (my copy): https://docs.google.com/presentation/d/1p5XNS7b9_R40zaBgC5EiWvP1Vs7UJiAXPQ3WP-U9PjI/edit?usp=sharing

# The Code

## Existing Code/Data

In [1]:
# !pip install -U fsds
from fsds.imports import *

import os
pd.set_option('display.max_columns',0)

fsds v0.3.2 loaded.  Read the docs: https://fs-ds.readthedocs.io/en/latest/ 


In [2]:
## Appending folder with functions
%load_ext autoreload 
%autoreload 2
# import sys
# sys.path.append('.')

import functions as fn
# help(fn)

In [3]:
## original class for using The Covid Tracking Project API
covid = fn.CovidTrackingProject(verbose=True)
covid

[i] DOWNLOADING DATASETS FROM COVID TRACKING PROJECT
	https://covidtracking.com/data
	- File saved as: "New Data/states_metadata.csv"
ERROR
	- File saved as: "New Data/us.csv"
	- File saved as: "New Data/states.csv"
states


------------------------------------------------------------
[i] CovidTrackingProject Contents:
------------------------------------------------------------

METHODS:
	download_state_daily
	download_state_meta
	download_us_daily
	get_csv_save_load
	get_df
	get_group_ts
	help

ATTRIBUTES
	base_folder
	base_url
	columns
	columns_us
	df
	df_states
	df_us
	urls

In [4]:
covid.df

states


state  positive  probableCases  ...  positiveScore  score grade
date                                       ...                            
2021-03-07    AK   56886.0            NaN  ...              0      0   NaN
2021-03-07    AL  499819.0       107742.0  ...              0      0   NaN
2021-03-07    AR  324818.0        69092.0  ...              0      0   NaN
2021-03-07    AS       0.0            NaN  ...              0      0   NaN
2021-03-07    AZ  826454.0        56519.0  ...              0      0   NaN
...          ...       ...            ...  ...            ...    ...   ...
2020-01-17    WA       0.0            NaN  ...              0      0   NaN
2020-01-16    WA       0.0            NaN  ...              0      0   NaN
2020-01-15    WA       0.0            NaN  ...              0      0   NaN
2020-01-14    WA       0.0            NaN  ...              0      0   NaN
2020-01-13    WA       NaN            NaN  ...              0      0   NaN

[20780 rows x 55 columns]

## Columns to Find

#### Columns to find from the covid tracking project dataset: 

- "hospitalizedCurrently"/"hospitalizedCumulative"
- "inIcuCurrently","inIcuCumulative"
- "onVentilatorCurrently","onVentilatorCumulative"

# New Data Sources

## Kaggle

### ❌ Covid19-US JHU Data by County + Demographics

- https://www.kaggle.com/headsortails/covid19-us-county-jhu-data-demographics

- **NOTE: after downloading it seems to just be county demographics, not any time series covid stats**

In [5]:
# !kaggle datasets download -d headsortails/covid19-us-county-jhu-data-demographics

In [6]:
# import zipfile
# us_county_jhu_zip = zipfile.ZipFile('covid19-us-county-jhu-data-demographics.zip')
# us_county_jhu_zip.namelist()

In [7]:
# us_county_jhu_zip.extract('us_county.csv')
# us_county = pd.read_csv("us_county.csv")
# us_county

In [8]:
# us_county_jhu_zip.extract('covid_us_county.csv')
# covid_us_county = pd.read_csv("covid_us_county.csv")
# covid_us_county

# **Cleaning File Organization/Downloading** 08/12

### Covid-19 Data From Johns Hopkins University

- https://www.kaggle.com/antgoldbloom/covid19-data-from-john-hopkins-university
- Comes with CONVENIENT_ files and RAW_ files.

In [9]:
## Specifying data storage folders
fpath_raw = r"data_raw"
fpath_clean = r"data/"
[os.makedirs(fpath,exist_ok=True) for fpath in [fpath_clean,fpath_raw]];
# sorted(os.listdir())

In [10]:
# # !kaggle datasets download  -p "{fpath_raw}" -d antgoldbloom/covid19-data-from-john-hopkins-university -f CONVENIENT_global_confirmed_cases.csv --force
# os.system(f"kaggle datasets download  -p {fpath_raw} -d antgoldbloom/covid19-data-from-john-hopkins-university -f CONVENIENT_global_confirmed_cases.csv --force")

### Files of Interest

In [11]:
# files = ['CONVENIENT_us_metadata.csv','RAW_us_confirmed_cases.csv','RAW_us_deaths.csv']
# for file in files:
#     print(f"Downloading {file} to {fpath_raw}")
#     os.system(f"kaggle datasets download  -p {fpath_raw} -d antgoldbloom/covid19-data-from-john-hopkins-university -f {file} --force")

## Previous Way - Entire Zip Archive

In [12]:
!kaggle datasets download -p "{fpath_raw}" -d antgoldbloom/covid19-data-from-john-hopkins-university

covid19-data-from-john-hopkins-university.zip: Skipping, found more recently modified local copy (use --force to force download)


In [13]:
import zipfile
jhu_data_zip = zipfile.ZipFile(os.path.join(fpath_raw,'covid19-data-from-john-hopkins-university.zip'))
jhu_data_zip.namelist()

['CONVENIENT_global_confirmed_cases.csv',
 'CONVENIENT_global_deaths.csv',
 'CONVENIENT_global_metadata.csv',
 'CONVENIENT_us_confirmed_cases.csv',
 'CONVENIENT_us_deaths.csv',
 'CONVENIENT_us_metadata.csv',
 'RAW_global_confirmed_cases.csv',
 'RAW_global_deaths.csv',
 'RAW_us_confirmed_cases.csv',
 'RAW_us_deaths.csv']

In [14]:
## Files to extract
import os 

files_to_extract = ['RAW_us_confirmed_cases.csv','CONVENIENT_us_confirmed_cases.csv',
                    'RAW_us_deaths.csv','CONVENIENT_us_deaths.csv','CONVENIENT_us_metadata.csv']
for i,file in enumerate(files_to_extract):
    print(f"{i}. {file}")
    jhu_data_zip.extract(file,path=fpath_raw)

0. RAW_us_confirmed_cases.csv
1. CONVENIENT_us_confirmed_cases.csv
2. RAW_us_deaths.csv
3. CONVENIENT_us_deaths.csv
4. CONVENIENT_us_metadata.csv


In [15]:
import os

## raw vs conv cases
raw_us_cases = pd.read_csv(files_to_extract[0],low_memory=False)
conv_us_cases = pd.read_csv(files_to_extract[1],low_memory=False)
display(raw_us_cases.head().style.set_caption('raw_us_cases'),
       conv_us_cases.head().style.set_caption('conv_us_cases'))

print('---'*30)

## raw vs conv deaths 
raw_us_deaths = pd.read_csv(files_to_extract[2],low_memory=False)
conv_us_deaths = pd.read_csv(files_to_extract[3],low_memory=False)
display(raw_us_deaths.head().style.set_caption('raw_us_deaths'),
       conv_us_deaths.head().style.set_caption('conv_us_deaths'))

------------------------------------------------------------------------------------------


In [16]:
# metadata
conv_metadata = pd.read_csv(files_to_extract[4],low_memory=False)
conv_metadata

Province_State      Admin2  Population        Lat        Long
0           Alabama     Autauga       55869  32.539527  -86.644082
1           Alabama     Baldwin      223234  30.727750  -87.722071
2           Alabama     Barbour       24686  31.868263  -85.387129
3           Alabama        Bibb       22394  32.996421  -87.125115
4           Alabama      Blount       57826  33.982109  -86.567906
...             ...         ...         ...        ...         ...
3337        Wyoming       Teton       23464  43.935225 -110.589080
3338        Wyoming       Uinta       20226  41.287818 -110.547578
3339        Wyoming  Unassigned           0   0.000000    0.000000
3340        Wyoming    Washakie        7805  43.904516 -107.680187
3341        Wyoming      Weston        6927  43.839612 -104.567488

[3342 rows x 5 columns]

### Notes re: kaggle source above

- **The RAW_ files** are closer to what I have been working with already so I will stick with those. 

In [17]:
jhu_data_zip = zipfile.ZipFile(os.path.join(fpath_raw,'covid19-data-from-john-hopkins-university.zip'))
jhu_data_zip.namelist()

['CONVENIENT_global_confirmed_cases.csv',
 'CONVENIENT_global_deaths.csv',
 'CONVENIENT_global_metadata.csv',
 'CONVENIENT_us_confirmed_cases.csv',
 'CONVENIENT_us_deaths.csv',
 'CONVENIENT_us_metadata.csv',
 'RAW_global_confirmed_cases.csv',
 'RAW_global_deaths.csv',
 'RAW_us_confirmed_cases.csv',
 'RAW_us_deaths.csv']

In [18]:
# metadata
file = 'CONVENIENT_us_metadata.csv'
jhu_data_zip.extract(file,path=fpath_raw)
df_metadata = pd.read_csv(os.path.join(fpath_raw,file))
df_metadata

Province_State      Admin2  Population        Lat        Long
0           Alabama     Autauga       55869  32.539527  -86.644082
1           Alabama     Baldwin      223234  30.727750  -87.722071
2           Alabama     Barbour       24686  31.868263  -85.387129
3           Alabama        Bibb       22394  32.996421  -87.125115
4           Alabama      Blount       57826  33.982109  -86.567906
...             ...         ...         ...        ...         ...
3337        Wyoming       Teton       23464  43.935225 -110.589080
3338        Wyoming       Uinta       20226  41.287818 -110.547578
3339        Wyoming  Unassigned           0   0.000000    0.000000
3340        Wyoming    Washakie        7805  43.904516 -107.680187
3341        Wyoming      Weston        6927  43.839612 -104.567488

[3342 rows x 5 columns]

### Adding State Abbreviations

- Adding 2 letter abbrevtions (more appropriate for column name prefix)


In [19]:
state_abbrevs = pd.read_csv('Reference Data/united_states_abbreviations.csv')
state_abbrevs.head()

State Abbreviation
0     Alabama           AL
1      Alaska           AK
2     Arizona           AZ
3    Arkansas           AR
4  California           CA

In [20]:
## Making dicts of Name:Abbrev and Abbrev:Name
state_to_abbrevs_map = dict(zip(state_abbrevs['State'],state_abbrevs['Abbreviation']))
abbrev_to_state_map = dict(zip(state_abbrevs['Abbreviation'],state_abbrevs['State']))

state_to_abbrevs_map.keys()

dict_keys(['Alabama', 'Alaska', 'Arizona', 'Arkansas', 'California', 'Colorado', 'Connecticut', 'Delaware', 'District of Columbia', 'Florida', 'Georgia', 'Hawaii', 'Idaho', 'Illinois', 'Indiana', 'Iowa', 'Kansas', 'Kentucky', 'Louisiana', 'Maine', 'Montana', 'Nebraska', 'Nevada', 'New Hampshire', 'New Jersey', 'New Mexico', 'New York', 'North Carolina', 'North Dakota', 'Ohio', 'Oklahoma', 'Oregon', 'Maryland', 'Massachusetts', 'Michigan', 'Minnesota', 'Mississippi', 'Missouri', 'Pennsylvania', 'Rhode Island', 'South Carolina', 'South Dakota', 'Tennessee', 'Texas', 'Utah', 'Vermont', 'Virginia', 'Washington', 'West Virginia', 'Wisconsin', 'Wyoming', 'Puerto Rico'])

In [21]:
df_metadata.isna().sum()

Province_State    0
Admin2            6
Population        0
Lat               0
Long              0
dtype: int64

In [22]:
## Adding State Abbrevas to kaggle metadata
df_metadata.insert(1,'State_Code',df_metadata['Province_State'].map(state_to_abbrevs_map))
df_metadata[df_metadata['State_Code'].isna()]

Province_State State_Code Admin2  Population      Lat      Long
102             American Samoa        NaN    NaN       55641 -14.2710 -170.1320
338           Diamond Princess        NaN    NaN           0   0.0000    0.0000
572             Grand Princess        NaN    NaN           0   0.0000    0.0000
573                       Guam        NaN    NaN      164229  13.4443  144.7937
2123  Northern Mariana Islands        NaN    NaN       55144  15.0979  145.6739
3009            Virgin Islands        NaN    NaN      107268  18.3358  -64.8963

- We do not have corresponding State codes for:
    -'American Samoa',
    'Diamond Princess', 
    'Grand Princess',
    'Guam',
    'Northern Mariana Islands',
    'Virgin Islands'
    
- We will exclude them from the final dataset. 

In [23]:
## Dropping us territories
df_metadata.dropna(subset=['State_Code'], inplace=True)
df_metadata.isna().sum()

Province_State    0
State_Code        0
Admin2            0
Population        0
Lat               0
Long              0
dtype: int64

In [24]:
df_metadata

Province_State State_Code      Admin2  Population        Lat        Long
0           Alabama         AL     Autauga       55869  32.539527  -86.644082
1           Alabama         AL     Baldwin      223234  30.727750  -87.722071
2           Alabama         AL     Barbour       24686  31.868263  -85.387129
3           Alabama         AL        Bibb       22394  32.996421  -87.125115
4           Alabama         AL      Blount       57826  33.982109  -86.567906
...             ...        ...         ...         ...        ...         ...
3337        Wyoming         WY       Teton       23464  43.935225 -110.589080
3338        Wyoming         WY       Uinta       20226  41.287818 -110.547578
3339        Wyoming         WY  Unassigned           0   0.000000    0.000000
3340        Wyoming         WY    Washakie        7805  43.904516 -107.680187
3341        Wyoming         WY      Weston        6927  43.839612 -104.567488

[3336 rows x 6 columns]

In [25]:
## Saving county info
df_metadata.to_csv(os.path.join(fpath_clean,"us_metadata_counties.csv"),index=False)

In [26]:
## Saving a states-only version with aggregated populations and mean lat/long
df_state_metadata = df_metadata.groupby('Province_State',as_index=False).agg({'Population':'sum',
                                               "Lat":'mean',"Long":"mean"})
df_state_metadata.insert(1,'State_Code',df_state_metadata['Province_State'].map(state_to_abbrevs_map))
df_state_metadata

Province_State State_Code  Population        Lat        Long
0                Alabama         AL     4903185  31.931113  -84.196785
1                 Alaska         AK      740995  56.628273 -139.571540
2                Arizona         AZ     7278717  29.714033  -98.349911
3               Arkansas         AR     3017804  34.005087  -90.033096
4             California         CA    39512223  36.582496 -116.704308
5               Colorado         CO     5758736  37.755612 -102.289687
6            Connecticut         CT     3565287  33.290944  -58.125464
7               Delaware         DE      973764  23.465566  -45.319942
8   District of Columbia         DC      705749  12.968059  -25.672187
9                Florida         FL    21477737  28.101892  -80.303621
10               Georgia         GA    10617423  32.400973  -82.539201
11                Hawaii         HI     1415872  15.020202 -112.373740
12                 Idaho         ID     1787065  42.338906 -109.483598
13              Illinois         IL    12671821  39.077394  -87.463362
14               Indiana         IN     6732219  38.989750  -84.384131
15                  Iowa         IA     3155070  41.197635  -91.614717
16                Kansas         KS     2913314  37.766026  -96.251195
17              Kentucky         KY     4467673  37.005387  -83.803171
18             Louisiana         LA     4648794  30.150233  -89.041636
19                 Maine         ME     1344212  39.722390  -61.798905
20              Maryland         MD     6045680  36.013773  -70.777355
21         Massachusetts         MA     6892503  37.117303  -63.016296
22              Michigan         MI     9986857  42.018626  -81.265296
23             Minnesota         MN     5639632  44.528372  -92.308909
24           Mississippi         MS     2976149  32.011947  -87.511304
25              Missouri         MO     6626371  37.804955  -90.931699
26               Montana         MT     1068778  45.354874 -105.917623
27              Nebraska         NE     1934408  40.451862  -96.953980
28                Nevada         NV     3080156  35.123787 -105.188836
29         New Hampshire         NH     1359711  36.232477  -59.648047
30            New Jersey         NJ     8882190  36.783272  -68.133541
31            New Mexico         NM     2096829  32.575110  -99.836416
32              New York         NY    19453561  41.214647  -73.115615
33        North Carolina         NC    10488084  34.925696  -77.942254
34          North Dakota         ND      762062  45.670106  -96.603961
35                  Ohio         OH    11689100  39.414877  -80.994621
36              Oklahoma         OK     3956971  34.603132  -94.789339
37                Oregon         OR     4217737  42.150695 -115.083398
38          Pennsylvania         PA    12801989  39.634946  -75.365598
39           Puerto Rico         PR     3754939  17.783793  -64.747252
40          Rhode Island         RI     1059361  29.753673  -51.045789
41        South Carolina         SC     5148714  32.542577  -77.609091
42          South Dakota         SD      884659  42.970557  -96.389735
43             Tennessee         TN     6829174  35.145203  -84.333285
44                 Texas         TX    28995881  31.413295  -97.882342
45                  Utah         UT     3205958  37.528405 -105.527566
46               Vermont         VT      623989  38.639559  -63.598833
47              Virginia         VA     8535519  37.009615  -77.350546
48            Washington         WA     7614893  44.929699 -114.830478
49         West Virginia         WV     1792147  37.452350  -77.788772
50             Wisconsin         WI     5822434  43.195275  -87.371008
51               Wyoming         WY      578759  39.639935  -98.580983

In [27]:
df_state_metadata.to_csv(os.path.join(fpath_clean,"us_metadata_states.csv"),index=False)

In [28]:
# state_to_abbrevs_map = dict(zip(state_abbrevs['State'],state_abbrevs['Abbreviation']))
# abbrev_to_state_map = dict(zip(state_abbrevs['Abbreviation'],state_abbrevs['State']))

In [29]:
## Making and saving remapping dicts
import joblib

state_to_abbrevs_meta = dict(zip(df_state_metadata['Province_State'],df_state_metadata['State_Code']))
abbrev_to_state_meta = dict(zip(df_state_metadata['State_Code'],df_state_metadata['Province_State']))

joblib.dump(state_to_abbrevs_meta, os.path.join(fpath_clean,'state_names_to_codes_map.joblib'))
joblib.dump(abbrev_to_state_meta, os.path.join(fpath_clean,'state_codes_to_names_map.joblib'))


['data/state_codes_to_names_map.joblib']

In [30]:
## save mapper fo state to code for function
mapper_path = os.path.join(fpath_clean,'state_names_to_codes_map.joblib')
mapper_path

'data/state_names_to_codes_map.joblib'

### Prep ` df_cases_ts`

In [31]:
def load_raw_ts_file(jhu_data_zip, file = 'RAW_us_confirmed_cases.csv',
                     mapper_path='data/state_names_to_codes_map.joblib',
                    verbose=True):
    
    if verbose: 
        print(f"Loading data from {file}")
    state_to_abbrevs_meta = joblib.load(mapper_path)
    
    ## Extract and load csv
    jhu_data_zip.extract(file)
    data = pd.read_csv(file)
    
    ## Drop states not included in metadata
    data.insert(1,'State_Code',data['Province_State'].map(state_to_abbrevs_meta))
    data.dropna(subset=['State_Code'],inplace=True)
    return data

In [32]:
df_cases = load_raw_ts_file(jhu_data_zip, file = 'RAW_us_confirmed_cases.csv',)
df_cases

Loading data from RAW_us_confirmed_cases.csv


Province_State State_Code      Admin2  ...  8/9/21 8/10/21 8/11/21
0           Alabama         AL     Autauga  ...    7788    7818    7854
1           Alabama         AL     Baldwin  ...   27477   27736   28020
2           Alabama         AL     Barbour  ...    2629    2649    2681
3           Alabama         AL        Bibb  ...    3016    3034    3056
4           Alabama         AL      Blount  ...    7603    7631    7658
...             ...        ...         ...  ...     ...     ...     ...
3337        Wyoming         WY       Teton  ...    3995    4003    4014
3338        Wyoming         WY       Uinta  ...    2511    2538    2543
3339        Wyoming         WY  Unassigned  ...       0       0       0
3340        Wyoming         WY    Washakie  ...     953     958     960
3341        Wyoming         WY      Weston  ...     698     699     700

[3336 rows x 580 columns]

In [33]:
# file = 'RAW_us_confirmed_cases.csv'
# jhu_data_zip.extract(file)
# df_cases = pd.read_csv(file)

# ## Drop states not included in metadata
# df_cases.insert(1,'State_Code',df_cases['Province_State'].map(state_to_abbrevs_map))
# df_cases.dropna(subset=['State_Code'],inplace=True)
# df_cases

In [34]:
# ## Preparing list of columns for pd.melt
# cols_to_drop=['iso2','iso3','code3','UID','Country_Region','Combined_Key',
#               'Lat','Long_','FIPS']
# id_cols = ['Province_State','State_Code','Admin2','FIPS']
# value_cols = [c for c in df_cases.columns if c not in [*cols_to_drop,*id_cols]]
# value_cols[:5]

In [35]:
# ## Melt df_cases into df_cases_ts and convert to time sereis
# df_cases_ts = pd.melt(df_cases, 
#                       id_vars=id_cols, 
#                       value_vars=value_cols,var_name="Date",
#                       value_name='Confirmed Cases')
# df_cases_ts['Date'] = pd.to_datetime(df_cases_ts['Date'])

# df_cases_ts = df_cases_ts.set_index(['Province_State','Date']).sort_index()
# df_cases_ts

#### New Function that combines both load_df...functions

In [36]:
def melt_df_to_ts(df_cases,value_name, var_name='Date',
                  multi_index_cols=['State_Code','Date'],
                  id_cols = ['Province_State',"State_Code",'Admin2'],
                  cols_to_drop=['iso2','iso3','code3','UID','Country_Region',
                                'Combined_Key','Lat','Long_','FIPS']):
    
#     value_cols = [c for c in df_cases.columns if c not in [*cols_to_drop,*id_cols]]
    
    ## Remove any cols not in the actual dataframe
    id_cols = [c for c in id_cols if c in df_cases.columns] 
    cols_to_drop = [c for c in cols_to_drop if c in df_cases.columns] 
    
    ## CHECKING FOR NON-DATE COLS TO REMOVE
    value_cols = [c for c in df_cases.columns if c not in [*id_cols,*cols_to_drop]]
    value_cols = list(filter(lambda x: len(x.split('/'))>1,value_cols))
    
    
    df_cases_ts = pd.melt(df_cases, 
                          id_vars=id_cols, value_vars=value_cols,
                          var_name=var_name, value_name=value_name)
    
    df_cases_ts['Date'] = pd.to_datetime(df_cases_ts['Date'])
    df_cases_ts = df_cases_ts.set_index(multi_index_cols).sort_index()
    return df_cases_ts

In [37]:
df_cases = load_raw_ts_file(jhu_data_zip, file = 'RAW_us_confirmed_cases.csv',)
df_cases_ts = melt_df_to_ts(df_cases,'Cases')
df_cases_ts

Loading data from RAW_us_confirmed_cases.csv


Province_State          Admin2  Cases
State_Code Date                                            
AK         2020-01-22         Alaska  Aleutians East      0
           2020-01-22         Alaska  Aleutians West      0
           2020-01-22         Alaska       Anchorage      0
           2020-01-22         Alaska          Bethel      0
           2020-01-22         Alaska     Bristol Bay      0
...                              ...             ...    ...
WY         2021-08-11        Wyoming           Teton   4014
           2021-08-11        Wyoming           Uinta   2543
           2021-08-11        Wyoming      Unassigned      0
           2021-08-11        Wyoming        Washakie    960
           2021-08-11        Wyoming          Weston    700

[1894848 rows x 3 columns]

#### Functionizing Cases Processing

### Prep ` df_deaths_ts`

In [38]:

df_deaths = load_raw_ts_file(jhu_data_zip,file = 'RAW_us_deaths.csv')
df_deaths_ts = melt_df_to_ts(df_deaths,'Deaths')
df_deaths_ts

Loading data from RAW_us_deaths.csv


Province_State          Admin2  Deaths
State_Code Date                                             
AK         2020-01-22         Alaska  Aleutians East       0
           2020-01-22         Alaska  Aleutians West       0
           2020-01-22         Alaska       Anchorage       0
           2020-01-22         Alaska          Bethel       0
           2020-01-22         Alaska     Bristol Bay       0
...                              ...             ...     ...
WY         2021-08-11        Wyoming           Teton      11
           2021-08-11        Wyoming           Uinta      14
           2021-08-11        Wyoming      Unassigned       0
           2021-08-11        Wyoming        Washakie      26
           2021-08-11        Wyoming          Weston       6

[1894848 rows x 3 columns]

In [39]:
# pd.concat([df_cases_ts.loc['Alabama','Confirmed Cases'],df_deaths_ts.loc['Alabama','Deaths']])

In [40]:
pd.concat([df_cases_ts,df_deaths_ts],axis=1)

Province_State          Admin2  ...          Admin2 Deaths
State_Code Date                                       ...                       
AK         2020-01-22         Alaska  Aleutians East  ...  Aleutians East      0
           2020-01-22         Alaska  Aleutians West  ...  Aleutians West      0
           2020-01-22         Alaska       Anchorage  ...       Anchorage      0
           2020-01-22         Alaska          Bethel  ...          Bethel      0
           2020-01-22         Alaska     Bristol Bay  ...     Bristol Bay      0
...                              ...             ...  ...             ...    ...
WY         2021-08-11        Wyoming           Teton  ...           Teton     11
           2021-08-11        Wyoming           Uinta  ...           Uinta     14
           2021-08-11        Wyoming      Unassigned  ...      Unassigned      0
           2021-08-11        Wyoming        Washakie  ...        Washakie     26
           2021-08-11        Wyoming          Weston  ...          Weston      6

[1894848 rows x 6 columns]

In [41]:
# id_cols = ['Province_State',"State_Code",'Admin2']
# cols_to_drop=['iso2','iso3','code3','UID','Country_Region',
#         'Combined_Key','Lat','Long_','FIPS']


# ## CHECKING FOR NON-DATE COLS TO REMOVE
# melt_cols = [c for c in df_deaths.columns if c not in [*id_cols,*cols_to_drop]]
# melt_cols = list(filter(lambda x: len(x.split('/'))>1,melt_cols))
# melt_cols

In [42]:
# ## Preparing list of columns for pd.melt
# cols_to_drop=['iso2','iso3','code3','UID','Country_Region','Combined_Key',
#               'Lat','Long_','FIPS','Population']
# id_cols = ['Province_State','Admin2',]
# value_cols = [c for c in df_deaths.columns if c not in [*cols_to_drop,*id_cols]]
# value_cols[:5]

In [43]:
# ## Melt df_cases into df_cases_ts and convert to time sereis
# df_deaths_ts = pd.melt(df_deaths,id_vars=id_cols, value_vars=value_cols,var_name="Date",
#                value_name='# Deaths')
# df_deaths_ts['Date'] = pd.to_datetime(df_deaths_ts['Date'])

# df_deaths_ts = df_deaths_ts.set_index(['Province_State','Date']).sort_index()
# df_deaths_ts

#### Functionizing Deaths Processing

In [44]:
# def load_df_deaths_ts(df_deaths, id_cols = ['Province_State','Admin2'],
#                       var_name='Date',value_name='# Deaths',
#                      cols_to_drop=['iso2','iso3','code3','UID',
#                                    'Country_Region','Combined_Key',
#                                    'Lat','Long_','FIPS','Population']):
#     value_cols = [c for c in df_deaths.columns if c not in [*cols_to_drop,*id_cols]]
#     df_deaths_ts = pd.melt(df_deaths,id_vars=id_cols, value_vars=value_cols,var_name=var_name,
#                    value_name=value_name)
#     df_deaths_ts['Date'] = pd.to_datetime(df_deaths_ts['Date'])

#     df_deaths_ts = df_deaths_ts.set_index(['Province_State','Date']).sort_index()
#     return df_deaths_ts

In [45]:
# file = 'RAW_us_deaths.csv'
# jhu_data_zip.extract(file)
# df_deaths = pd.read_csv(file)
# df_deaths_ts = load_df_deaths_ts(df_deaths)
# df_deaths_ts

### Join Dataset and Make STATES dict

In [46]:
unique_states = list(abbrev_to_state_meta.keys())
len(unique_states)

52

In [47]:
# unique_states = np.unique(df_deaths_ts.index.get_level_values(0))
# len(unique_states)

In [48]:
print(unique_states)

['AL', 'AK', 'AZ', 'AR', 'CA', 'CO', 'CT', 'DE', 'DC', 'FL', 'GA', 'HI', 'ID', 'IL', 'IN', 'IA', 'KS', 'KY', 'LA', 'ME', 'MD', 'MA', 'MI', 'MN', 'MS', 'MO', 'MT', 'NE', 'NV', 'NH', 'NJ', 'NM', 'NY', 'NC', 'ND', 'OH', 'OK', 'OR', 'PA', 'PR', 'RI', 'SC', 'SD', 'TN', 'TX', 'UT', 'VT', 'VA', 'WA', 'WV', 'WI', 'WY']


In [50]:
# df_cases_ts.loc[state]

In [51]:
# state='NY'
# df_cases_temp = df_cases_ts.loc[state].reset_index()
# df_deaths_temp = df_deaths_ts.loc[state].reset_index()

# ## Merge using date and Admin2/county
# df_merged = pd.merge(df_cases_temp, df_deaths_temp, on=['Date','Admin2'])
# df_merged_ts = df_merged.set_index("Date").resample('D').sum()

# df_merged_ts.columns = [f"{c}-{state}" for c in df_merged_ts.columns]
# df_merged_ts

In [ ]:
STATES = {}

for state in unique_states:
    ## Reset the state's datafranes for pd.merge
    df_cases_temp = df_cases_ts.loc[state].reset_index()
    df_deaths_temp = df_deaths_ts.loc[state].reset_index()

    ## Merge using date and Admin2/county
    df_merged = pd.merge(df_cases_temp, df_deaths_temp, on=['Date','Admin2'])
    df_merged_ts = df_merged.set_index("Date").resample('D').sum()

    df_merged_ts.columns = [f"{c}-{state}" for c in df_merged_ts.columns]    
    
    STATES[state] = df_merged_ts.copy()

STATES.keys()

In [ ]:
STATES['NY']

In [ ]:
df_cumulative = STATES['NY'].copy()
df_cumulative.plot(subplots=True)

In [ ]:
df_diff = STATES['NY'].copy().diff().fillna(0)
df_diff.plot(subplots=True)

### Saving CSVs

In [ ]:
import os
# folder = "./data/"
folder = os.path.join(fpath_clean,'state_data/')
os.makedirs(folder,exist_ok=True)
os.listdir(folder)

### Test Join- Maryland Deaths and Cases Data

In [ ]:
# ## Testing md data -  reset index for multi-column join
# md_cases = df_cases_ts.loc['Maryland'].reset_index()
# md_cases

In [ ]:
# ## Testing md data -  reset index for multi-column join
# md_deaths = df_deaths_ts.loc['Maryland'].reset_index()
# md_deaths

In [ ]:
# df_md = pd.merge(md_cases, md_deaths, on=['Date','Admin2'])
# df_md = df_md.set_index("Date").resample('D').sum()

# df_md.plot(subplots=True)

In [ ]:
# df_md_diff = df_md.diff().fillna(0)#.plot(subplots=True)
# df_md_diff.plot(subplots=True)

- 

___

# BOOKMARK - Data.Gov From BEFORE Kaggle

## Data.Gov Hospital Data

### ❌"COVID-19 Reported Patient Impact and Hospital Capacity by State" [NOT TIME SERIES!!!]

- https://healthdata.gov/dataset/COVID-19-Reported-Patient-Impact-and-Hospital-Capa/6xf2-c3ie

In [ ]:
# ## JSON way - From https://dev.socrata.com/foundry/healthdata.gov/6xf2-c3ie

# #!/usr/bin/env python

# # make sure to install these packages before running:
# # pip install pandas
# # pip install sodapy

# import pandas as pd
# from sodapy import Socrata

# # Unauthenticated client only works with public data sets. Note 'None'
# # in place of application token, and no username or password:
# client = Socrata("healthdata.gov", None)

# # Example authenticated client (needed for non-public datasets):
# # client = Socrata(healthdata.gov,
# #                  MyAppToken,
# #                  userame="user@example.com",
# #                  password="AFakePassword")

# # First 2000 results, returned as JSON from API / converted to Python list of
# # dictionaries by sodapy.
# results = client.get("6xf2-c3ie", limit=2000)

# # Convert to pandas DataFrame
# results_df = pd.DataFrame.from_records(results)
# results_df

In [ ]:
# ## CSV way
# url ="https://healthdata.gov/resource/6xf2-c3ie.csv"
# df0 = pd.read_csv(url,parse_dates=True)
# df0


In [ ]:
# df0.info()

In [ ]:
# df0.nunique()

### `"COVID-19 Reported Patient Impact and Hospital Capacity by State Timeseries API"`
- https://healthdata.gov/Hospital/COVID-19-Reported-Patient-Impact-and-Hospital-Capa/g62h-syeh

- API URL (csv): https://healthdata.gov/resource/g62h-syeh.csv
- ~~geojson url: https://healthdata.gov/resource/g62h-syeh.geojson~~

In [ ]:
df1_downloaded = pd.read_csv('/Users/jamesirving/Downloads/COVID-19_Reported_Patient_Impact_and_Hospital_Capacity_by_State_Timeseries.csv')
df1_downloaded

### Why do I get more data if I download? Pagination?
- https://dev.socrata.com/docs/paging.html

In [ ]:
# base_url = 'https://healthdata.gov/resource/g62h-syeh.csv'
# df1 = pd.read_csv(base_url)
# df1['date'] = pd.to_datetime(df1['date'])
# df1.sort_values('date')

In [ ]:
# url =base_url+"?$offset=1000"
# pd.read_csv(url)

In [ ]:
## Getting Hospital Capacity Data
# base_url = 'https://healthdata.gov/resource/g62h-syeh.csv'
# df1 = pd.read_csv(base_url)
# df1['date'] = pd.to_datetime(df1['date'])
# df1 = df1.sort_values(['state','date'])
# df1

# 🎗**BOOKMARK 08/12 - SIMPLIFYING HHS DATA WORKFLOW**

### Def Function to Get Pages of Data from HHS

In [ ]:
def get_hospital_data():
    offset = 0
    ## Getting Hospital Capacity Data
    base_url = 'https://healthdata.gov/resource/g62h-syeh.csv'
    page = 0
    results = []

    ## seting random, large page-len
    page_len = 1000

    while (page_len>0):
        print(f"[i] Page {page}")
        print(f' - offset = {offset}')
        url = base_url+f"?$offset={offset}"
        df_temp = pd.read_csv(url)
        results.append(df_temp)

        page_len = len(df_temp)
        offset+=page_len
        page+=1
    return pd.concat(results)

# hospital_df = get_hospital_data()
# hospital_df

In [ ]:

df1 = get_hospital_data()
df1['date'] = pd.to_datetime(df1['date'])
df1 = df1.sort_values(['state','date'])
df1

In [ ]:
raise Exception("Stop here for today!")

In [ ]:
[c for c in df1.columns if 'vent' in c]

In [ ]:
unique_states_hospitals = df1['state'].unique()
unique_states_hospitals

In [ ]:
# df1 = df1.set_index(['state','date'])
# df1

- Need to reconcile what dates are and are not included

In [ ]:
# md = df1.loc['MD']
# # md = md.set_index('date').sort_index(ascending=False)
# md

In [ ]:
## Dropping cols with # hospitals reporting ('coverage')
coverage_cols = [c for c in df1.columns if "coverage" in c]
df1.drop(columns=coverage_cols,inplace=True)

#### [Column Notes](https://healthdata.gov/Hospital/COVID-19-Reported-Patient-Impact-and-Hospital-Capa/g62h-syeh)
- General Naming Schemes:
    - "...coverage" columns:
        - coverage columns seem to all represent # of hospitals reporting for that stat. 
    - "...utilization" columns:
        - seem to be the metrics I am looking for
            - have "utilization",+'_denominator'+'numerator" columns for each
    
    
    
- Groups of columns:
    - "critical_staffing_shortage" columns:
        - "critical_staffing_shortage_today"...
            - yes, no, not_reported
        - "critical_staffing_anticipated_within_week"....
            - yes,no,not_reported
    - "hospital_onset"...
    - "inpatient_beds"...
    - "previous_day_admission"..
        

### Columns to find from the covid tracking project dataset: 

- Old: "hospitalizedCurrently"/"hospitalizedCumulative"
    - New: "inpatient_beds_utilization"
- "inIcuCurrently","inIcuCumulative"
    - New: "adult_icu_bed_utilization
- "onVentilatorCurrently","onVentilatorCumulative"

In [ ]:
## collecting lists of colun names (see md cell above with notes )

## unneeded cols
staffing_cols = [c for c in df1.columns if "staffing" in c]
previous_day_cols = [c for c in df1.columns if "previous_day" in c]


## unsure/raw util cols
raw_inpatient_beds =  ['inpatient_beds','inpatient_beds_used','inpatient_beds_used_covid']


## needed cols (utilization )
inpatient_bed_util_cols = [c for c in df1.columns if 'inpatient_beds_utilization' in c]
adult_icu_util_cols = [c for c in df1.columns if 'adult_icu_bed_utilization'in c]



## COMBINING ABOVE LISTS INTO DROP AND KEEP LISTS
DROP_COLS = [*staffing_cols,*previous_day_cols]
UNSURE_COLS = [*raw_inpatient_beds]

KEEP_COLS = ['date','state',*inpatient_bed_util_cols,*adult_icu_util_cols]
KEEP_COLS

In [ ]:
## SHOWING UN-CAPTURED COLUMNS
df1.drop(columns=[*DROP_COLS,*KEEP_COLS,*UNSURE_COLS]).info()

### Making `df_hospitals`

In [ ]:
## Making df_hospitals
df_hospitals = df1[KEEP_COLS].copy()
df_hospitals = df_hospitals.set_index(['state','date']).sort_index()
df_hospitals.loc['MD',['inpatient_beds_utilization']].plot()

### Saving My CSVs

### Testing Data using 1 state

In [ ]:
df1['state'].value_counts().sort_index().head(15)

In [ ]:
## Processing 1 state
state = df1.groupby('state').get_group('MD')
state = state.set_index('date').sort_index()
state

In [ ]:
# state = state.resample('D').asfreq()
# state['inpatient_beds'].plot()

#### Notes:
- Contains only 15 rows of data per state (?)
    - Try changing the arguments for the API 
        - [Api Docs[(https://dev.socrata.com/foundry/healthdata.gov/g62h-syeh)
    